In [24]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import json
import re
import string
import copy

import collections
from collections import Counter

from ingredient_parser import en

from pprint import pprint

import nltk
from nltk.tokenize import sent_tokenize, word_tokenize
from nltk.corpus import stopwords

In [26]:
# Add KB

# TO DO - Increase versus most_common ingredients that are not represented
ingredientsKB = {}

ingredientsKB['dairyIngredients'] = ['buttermilk', 'cottage', 'cream', 'creamer', 'creamy', 'creme', 'ghee', 'half-and-half', 'milk', 'yogurt']

ingredientsKB['cheeses'] = ['cheese','parmesan','bocconcini', 'mozzarella', 'gouda', 'swiss', 'brie']

ingredientsKB['meats'] = ['beef','bacon', 'beefs', 'burgers', 'chorizo', 'dogs', 'frankfurters', 'giblets', 'ham', 'lambs', 'livers', 'meatballs', 'meatloaves', 'meats', 'mignon', 'mincemeat', 'pepperonis', "pig's", 'porks', 'prosciutto', 'ribs', 'roasts', 'sausages', 'sirloin', 'tripe', 'veal', 'venison', 'kielbasas', 'liverwurst', 'wieners', 'cotechino', 'linguica', 'pastrami', 'squirrels', 'sauerbraten', 'picadillo', 'carcass', 'brains', 'mortadella', 'rounds', 'sweetbread', 'toad', 'tinga', 'embutido', 'hash', 'broil', 'brisket', 'franks', 'pigs', 'rouladen', 'chops', 'scrapple', 'barbeque', 'spareribs']
ingredientsKB['poultry'] = ['chicken','bologna', 'bratwursts', 'chickens', 'ducks', 'goose', 'hens', 'pollo', 'salami', 'turkey', 'pheasant', 'quail', 'turducken', 'drumettes', 'wings', 'roosters']
ingredientsKB['fish'] = ['albacores', 'bass', 'catfish', 'cods', 'fish', 'flounder', 'grouper', 'haddock', 'halibut', 'mahi', 'monkfish', 'salmon', 'shark', 'snapper', 'sole', 'swordfishes', 'trouts', 'tunas', 'bluefish', 'bonito', 'rockfish', 'mackerel', 'naruto', 'drum', 'marlin', 'tilapia', 'carp', 'kingfish', 'mullets', 'whitefish', 'kippers', 'torsk', 'saltfish']
ingredientsKB['seafoods'] = ['seafood','anchovies', 'calamaris', 'clams', 'crabs', 'crabmeat', 'crawfish', 'lobsters', 'mussels', 'oysters', 'prawns', 'scallops', 'seafood', 'shrimps', 'squids', 'snails', 'shellfish', 'caviar']
ingredientsKB['mainProteins'] = ['beans', 'chickpeas', 'nuts', 'seeds', 'tofu', 'whey', 'buckwheat', 'protein', 'soybeans', 'soy', 'tempeh', 'lentils', 'masoor', 'gluten', 'pine', 'falafel', 'portobello']
ingredientsKB['fruits'] = ['apples', 'apricots', 'bananas', 'blackberries', 'blueberries', 'cantaloupe', 'cherries', 'citrons', 'citrus', 'coconuts', 'cranberries', 'currants', 'elderberries', 'figs', 'fruitcakes', 'fruits', 'gooseberries', 'grapefruit', 'grapes', 'guava', 'honeydew', 'huckleberries', 'kiwis','kumquats', 'lemonade', 'lemons', 'limes', 'mangoes', 'marrons', 'mincemeat', 'mulberries', 'nectarines', 'oranges', 'papayas', 'peaches', 'pears', 'persimmon', 'persimmons', 'pineapples', 'plums', 'prunes', 'raisins',  'raspberries', 'slushies', 'smoothies', 'sorrel', 'strawberries', 'tangerines', 'watermelons', 'yuzu', 'lingonberries', 'plantains', 'juniper', 'lingonberries', 'pomegranates', 'serviceberries', 'zinfandel', 'lychees', 'carambola', 'uvas']
ingredientsKB['vegetables'] = ['artichokes', 'arugula', 'asparagus', 'avocados', 'bamboo', 'beets', 'broccoli', 'cabbage', 'calzones', 'carrots', 'cauliflower', 'celery', 'chilis', 'chives', 'choy', 'cilantro', 'coleslaw', 'coriander', 'cucumber', 'cucumbers', 'dates', 'eggplant', 'eggplants', 'endive', 'escarole', 'galangal', 'haystacks', 'jicama', 'kale', 'kohlrabi', 'kucai', 'leeks', 'lettuce', 'mushrooms', 'okra', 'olives', 'onions', 'parsley', 'parsnips', 'peas', 'peppers', 'pickles', 'pizzas', 'potatoes', 'pumpkins', 'radishes', 'rutabagas', 'salad', 'sauerkraut', 'shallots', 'slaws', 'spinach', 'sprouts', 'squash', 'tamarind', 'taros', 'tomatillo', 'tomatillos', 'tomatoes', 'turnips', 'vegetable', 'vegetables', 'veggies', 'watercress', 'yams', 'zucchinis', 'chervil', 'daikon', 'iceberg', 'nopales', 'pimentos', 'radicchio', 'karengo', 'nori', 'succotash', 'truffle', 'chard', 'fries', 'leaves', 'browns', 'romain', 'palm', 'sorghum', 'aloo', 'haricots', 'caprese', 'salata', 'shiitake']
ingredientsKB['sugars'] = ['Jell-O®', 'butterscotch', 'candied', 'candy', 'caramels', 'frosting', 'fructose', 'gingersnaps', 'glaces', 'glaze', 'glycerin', 'glycerol', 'gumdrops', 'gummi', 'honey', 'icing', 'jellybeans', 'ladyfingers', 'licorice', 'macaroons', 'maple', 'marrons glaces', 'marshmallows', 'marzipan', 'molasses', 'pastries', 'pectin', 'peppermints', 'pie', 'piping', 'puddings', 'puff', 'sourball', 'sprinkles', 'sucanat', 'sugar', 'sweetener', 'syrup', 'tarts', 'toffee', 'twinkies', 'colaciones', 'sherbet', "hershey®'s", 'candies', "confectioners'", 'fudge', 'taffy', 'pink', 'sherbet']
ingredientsKB['sauces'] = ['alfredo', 'applesauce', 'chutney', 'cannoli', 'dips', 'guacamole', 'hummus', 'paste', 'spreads', 'tahini', 'tzatziki', 'denjang', 'salsa', 'sauce', 'tapenade', 'coating', 'teriyaki', 'aioli', 'checca', 'amatriciana', 'ragu', 'marinara']
ingredientsKB['condiments'] = ['dressing', 'jam', 'ketchup', 'marinade', 'marjoram', 'mayonnaise', 'mirin', 'mustard', 'pesto', 'relish', 'shoyu', 'tamari', 'vinaigrette', 'gochujang']
ingredientsKB['soups'] = ['broth', 'chowder', 'dashi', 'soup', 'stew', 'jambalaya', 'gumbo', 'gazpacho', 'goulash', 'pho', 'slumgullion', 'cioppino', 'minestrone']
ingredientsKB['nuts'] = ['almonds', 'butternuts', 'candlenuts', 'cashews', 'chestnuts', 'hazelnuts', 'macadamia', 'nuts', 'peanuts', 'pecans', 'pistachios', 'walnuts', 'nuts']
ingredientsKB['alcoholicIngredients'] = ['anisette', 'beer', 'bitters', 'bourbon', 'brandy', 'cacao', 'chambord', 'champagne', 'cognac', 'eggnog', 'kirsch', 'kirschwasser', 'liqueur', 'rum', 'schnapps', 'sherry', 'ale', 'spritz', 'tequila', 'vermouth', 'vodka', 'whiskey', 'wine', 'campari', 'alcohol', 'absinthe', 'cachaca', 'liquor', 'cointreau', 'curacao', 'sake', 'sec', 'calvados', 'galliano', 'lillet', 'margaritas', 'coladas', 'negroni', 'mojitos', 'mimosas', 'bahama', 'slammer', 'sauvignon', 'chablis', 'martinis', 'tequinis', 'spritzs', 'cosmopolitan', 'hurricanes', 'sangria', 'sex', "shaggy's", 'nipples', 'stoli']
ingredientsKB['spices'] = ['allspice', 'anise', 'arrowroot', 'basil', 'bay', 'capers', 'caraway', 'cardamom', 'cassava', 'cayenne', 'chocolate', 'cilantro', 'cinnamon', 'cloves', 'cocoa', 'coriander', 'cumin', 'dill', 'fennel', 'flax', 'garlic', 'ginger', 'herbs', 'kalonji', 'mace', 'masala', 'miso', 'monosodium', 'nutmeg', 'oregano', 'paprika', 'pepper', 'peppercorns', 'pimento', 'poppy', 'poppyseed', 'powder','rhubarb', 'rosemary', 'saffron', 'sage', 'salt', 'savory', 'seasoning', 'sesame', 'spices', 'sunflower', 'tarragon', 'thyme', 'turmeric', 'vanilla', 'watercress', 'spearmint', 'comfort']
ingredientsKB['spicy'] = ['angelica', 'dijon', 'horseradish', 'jerk', 'wasabi', 'spicy']
ingredientsKB['hotPeppers'] = ['jalapenos', 'pepperoncinis', 'chiles']
ingredientsKB['grains'] = ['bagels', 'baguettes', 'barley', 'biscuits', 'bran', 'bread', 'buns', 'cereal', 'corn', 'cornbread', 'cornstarch', 'couscous', 'crackers', 'croutons', 'crusts', 'dough', 'granola', 'hominy', 'kasha', 'masa', 'matzo', 'millet', 'muffins', 'oats', 'pitas', 'popcorn', 'pretzels', 'quinoa', 'rice', 'rolls',  'shortbread', 'sourdough', 'stuffing', 'tapioca', 'toasts', 'tortillas', 'wheat', 'kaiser', 'cornmeal', 'breadcrumbs', 'graham', 'bulgur', 'farina', 'oatmeal', 'croissants', 'polenta', 'grits', 'pumpernickel', 'sago', 'seitan', 'grains', 'taters', 'risotto', 'shells', 'amarettini', 'mochi', 'cornflakes', 'pilaf', 'puppies']
ingredientsKB['pastas'] = ['farfalle', 'fettuccine', 'lasagnas', 'linguine', 'mac', 'macaroni', 'manicotti', 'noodles', 'pasta', 'farfel', 'vermicelli', 'tagliatelle', 'cannelloni', 'penne']
ingredientsKB['wrappedMeals'] = ['burritos', 'calzones', 'dumplings', 'empanadas', 'fajitas', 'hero', 'pie', 'pinwheels', 'pizzas', 'quesadillas', 'sandwiches', 'tacos', 'tourtiere', 'wontons', 'hoagie', 'pierogies', 'rarebit', 'joes', 'enchiladas', 'pierogi', 'bierrocks', 'torta', 'reuben', 'wraps', 'piroshki', 'tamales', 'bruschetta', 'antipasto', 'hamburger', 'muffuletta', 'blanket', 'runzas', 'samosas', 'sambousas', 'chalupas', 'spanakopita', 'submarine']
ingredientsKB['pastaDishes'] = ['casseroles', 'curry', 'lasagna', 'marzetti', 'mostaccioli', 'spaghetti', 'stroganoff', 'ziti', 'pastini', 'pastitsio', 'fideo', 'spaghettini', 'moussaka', 'tortellinis', 'tallerine', 'talerine', 'scampi', 'ravioli', 'pad', 'gnocchi', 'spaetzle', 'stromboli']
ingredientsKB['vegetableDishes'] = ['tabbouleh', 'kabobs', 'suey', 'frittatas', 'quiches', 'raita', 'shieldzini', 'stir', 'sukiyaki']
ingredientsKB['drinks'] = ['beverage', 'cider', 'coffee', 'dew™', 'drink', 'eggnog', 'epazote', 'espresso', 'gin', 'juices', 'lemonade', 'limeade', 'milk', 'rosewater', 'tea', 'wassail', 'punch', 'shake', 'shirley', 'americano']
ingredientsKB['cookingLiquids'] = ['oil', 'vinegar', 'water', 'snow', 'ice']
ingredientsKB['bakingIngredients'] = ['ammonia', 'baking', 'eggs', 'flour', 'margarine', 'yeast', 'bisquick®']
ingredientsKB['cookingFats'] = ['butter', 'gelatin', 'gravy', 'lard', 'lecithin', 'ovalette', 'shortening', 'xanthan', 'suet']
ingredientsKB['extras'] = ['carnations', 'coloring', 'dust', 'flowers', 'lilies', 'spray', 'toppings', 'drippings', 'powdered', 'gold']
ingredientsKB['fasteners'] = ['sticks', 'skewers', 'toothpicks']
ingredientsKB['adhesives'] = ['glue']
ingredientsKB['containers'] = ['jars']
ingredientsKB['flavorings'] = ['extract', 'flavorings', 'mint', 'pandan', 'hickory', 'flavored', 'mesquite', 'wood', 'hardwood']
ingredientsKB['mixtures'] = ['food', 'mixes']

# words with succeeding noun ("milk" or "cake")
ingredientsKB['nonDairyMilks'] = ['almond', 'soy', 'coconut']
ingredientsKB['cakeTypes'] = ['pound', 'sponge', 'white', 'yellow', 'bunny', "'scratch'"]


In [5]:
# Write KB to JSON

with open("ingredients_kb.json", 'w') as outfile:
    json.dump(ingredientsKB, outfile)


In [8]:
# Load in recipes 

# contains significant amount of info per recipe - needs to be cleaned before working with
df_rec = pd.read_json("../allrecipes-recipes.json",lines=True)

# simple - contains cusinse and recipes
df_rec_2 = pd.read_json("train.json")

In [13]:
df_rec.columns

Index(['author', 'cook_time_minutes', 'description', 'error', 'footnotes',
       'ingredients', 'instructions', 'photo_url', 'prep_time_minutes',
       'rating_stars', 'review_count', 'time_scraped', 'title',
       'total_time_minutes', 'url'],
      dtype='object')

In [11]:
# try filtering out pizza
df_rec = df_rec[~df_rec['description'].str.contains('pizza')]



In [9]:
def simple_list_full_rec(df,col_string):
    ingredients = []
    
    # iterate through all lists in df
    for raw_ings in df[col_string].tolist():
        #print(raw_ings)
        # iterate through each ingredient description
        for raw in raw_ings:
            # parse only the name using our parser
            raw_dict = en.parse(raw)
            #print(raw_dict['name'])
            ingredients.append(raw_dict['name'])
            
    # return the cleaned ingredients 
    return ingredients

In [19]:
def simple_list_from_df(df,col_string):
    ingredients = []
    for i in df[col_string].tolist():
        for j in i:
            ingredients += (j.lower().split())
    
    return ingredients


In [20]:
all_ingredients = simple_list_full_rec(df_rec,'ingredients') +simple_list_from_df(df_rec_2,'ingredients')

In [40]:
not_kb = Counter()

simple_kb = []

for i in ingredientsKB.values():
    simple_kb.extend(i)

    
    

In [42]:
for i in all_ingredients:
    if i not in simple_kb:
        not_kb[i] += 1

In [43]:
pprint(not_kb.most_common())

[('ground', 18256),
 ('fresh', 17853),
 ('all-purpose flour', 16739),
 ('white sugar', 15762),
 ('vanilla extract', 10953),
 ('olive', 10921),
 ('black', 10557),
 ('olive oil', 9864),
 ('red', 9189),
 ('green', 8531),
 ('chopped', 7884),
 ('vegetable oil', 7739),
 ('ground cinnamon', 7309),
 ('egg', 7309),
 ('juice', 7146),
 ('onion', 7016),
 ('garlic, minced', 6831),
 ('baking powder', 6601),
 ('baking soda', 6053),
 ('lemon', 5919),
 ('ground black pepper', 5686),
 ('large', 5396),
 ('lemon juice', 5144),
 ('dried', 5118),
 ('lime', 4994),
 ('all-purpose', 4635),
 ('chili', 4318),
 ('onion, chopped', 4282),
 ('bell', 4259),
 ('brown sugar', 4193),
 ('salt and pepper to taste', 3838),
 ('garlic powder', 3799),
 ('packed brown sugar', 3404),
 ('butter, softened', 3326),
 ('grated', 3280),
 ('salt and ground black pepper to taste', 3203),
 ('kosher', 3180),
 ("confectioners' sugar", 3114),
 ('sour cream', 3111),
 ('dry', 3046),
 ('grated Parmesan cheese', 3032),
 ('brown', 3010),
 ('gro

 ('fresh mushrooms, quartered', 36),
 ('(8 ounce) package angel hair pasta', 36),
 ('chopped fresh parsley, divided', 36),
 ('cubed Cheddar cheese', 36),
 ('leaves fresh basil', 36),
 ('potatoes, quartered', 36),
 ('Granny Smith apples - peeled, cored and sliced', 36),
 ('diced potatoes', 36),
 ('turnip', 36),
 ('zucchini, cubed', 36),
 ('garlic cloves, peeled', 36),
 ('parsley flakes', 36),
 ('minced fresh oregano', 36),
 ('seasoned croutons', 36),
 ('boneless, skinless chicken thighs', 36),
 ('plum tomatoes, diced', 36),
 ('beef short ribs', 36),
 ('(16 ounce) package egg noodles', 36),
 ('(15 ounce) can black beans', 36),
 ('(10 ounce) package frozen peas', 36),
 ('jalapeno peppers, chopped', 36),
 ('shredded iceberg lettuce', 36),
 ('tomato, thinly sliced', 36),
 ('cucumber, diced', 36),
 ('dried red chile peppers', 36),
 ('(.25 ounce) envelope active dry yeast', 36),
 ('celery ribs, thinly sliced', 36),
 ('ADDITIONAL INGREDIENTS:', 36),
 ('hamburger buns, split and toasted', 36),


 ('cucumbers, thinly sliced', 17),
 ('fresh dill, chopped', 17),
 ('lemon peel', 17),
 ('ears corn', 17),
 ('(10.5 ounce) can condensed cream of chicken soup', 17),
 ('(4 ounce) can sliced black olives, drained', 17),
 ('red pepper sauce', 17),
 ('liquid smoke flavoring (optional)', 17),
 ('crushed peppermint candies', 17),
 ('(750 milliliter) bottle dry white wine', 17),
 ('jalapeno peppers, seeded and diced', 17),
 ('DOUGH:', 17),
 ('(14 ounce) can NESTLE® CARNATION® Sweetened Condensed Milk', 17),
 ('plum tomatoes, seeded and chopped', 17),
 ('McCormick® Ground Ginger', 17),
 ('Rice:', 17),
 ('diced pineapple', 17),
 ('fresh oregano leaves', 17),
 ('(10 ounce) package fresh spinach, torn', 17),
 ('chopped plum tomatoes', 17),
 ('triple sec (orange-flavored liqueur)', 17),
 ('red bell pepper, coarsely chopped', 17),
 ('Powdered sugar (optional)', 17),
 ('PLANTERS Chopped Pecans', 17),
 ('chovy fillets', 17),
 ('(6 ounce) READY CRUST® Graham Cracker Pie Crust', 17),
 ('grated Parmesan

 ('(14 ounce) package caramels, unwrapped', 10),
 ('potatoes, peeled and cut into large chunks', 10),
 ('medium carrots, peeled and chopped', 10),
 ('cracked black peppercorns', 10),
 ('boneless, skinless chicken breast halves, cut into bite-sized pieces', 10),
 ('finely chopped dates', 10),
 ('instant chicken bouillon granules', 10),
 ('pear nectar', 10),
 ('dried Italian seasoning, crushed', 10),
 ('powdered sugar (optional)', 10),
 ('chopped onion, divided', 10),
 ('broiler/fryer chicken (3 to 4 pounds), cut up', 10),
 ('(6 ounce) package stuffing mix', 10),
 ('fat-free vanilla yogurt', 10),
 ('boneless skinless chicken breast halves (1-1/2 pounds)', 10),
 ('kiwifruit, peeled and sliced', 10),
 ('(14.5 ounce) cans reduced sodium chicken broth', 10),
 ('pastry for double-crust pie', 10),
 ('(14.5 ounce) can stewed tomatoes, cut up', 10),
 ('(15 ounce) can white kidney or cannelini beans, rinsed and drained', 10),
 ('(6 ounce) jar sliced mushrooms, drained', 10),
 ('(2.8 ounce) can Fr

 ('Salmon:', 7),
 ("(16 ounce) can BUSH'S® Pinto Beans, drained and rinsed", 7),
 ("(15.5 ounce) can BUSH'S® Cannellini Beans, drained and rinsed", 7),
 ('semi-sweet baking chocolate', 7),
 ('Mint leaves', 7),
 ('Mustard', 7),
 ('yellow pepper, chopped', 7),
 ('(14.5 ounce) can diced tomatoes in juice', 7),
 ('(14 ounce) can artichoke hearts, drained, chopped', 7),
 ('peanuts, chopped', 7),
 ('butter, slightly softened', 7),
 ('(15 ounce) can DOLE® Mandarin Oranges, drained', 7),
 ('bow tie pasta, uncooked', 7),
 ("Smucker's® Apricot Preserves", 7),
 ('loaf Italian bread', 7),
 ('pecans, finely chopped', 7),
 ('fresh goat cheese', 7),
 ('small pretzels', 7),
 ('peach, sliced', 7),
 ('(1.5 fluid ounce) jigger spiced rum', 7),
 ('(14.5 ounce) can whole berry cranberry sauce', 7),
 ('skinless, boneless chicken breast, cut in bite-sized pieces', 7),
 ('medium tomato, seeded and diced', 7),
 ('thinly sliced fresh mushrooms', 7),
 ('finely grated fresh orange zest', 7),
 ('cinnamon chips', 7

...

 ('Himalayan salt and cracked black pepper to taste', 1),
 ('salt (such as Real Salt®)', 1),
 ('hot popcorn, or as desired', 1),
 ('fresh okra, cut into 1-inch pieces, or more to taste', 1),
 ('cherry tomatoes, quartered, or more as desired', 1),
 ('sliced mushrooms, or to taste (optional)', 1),
 ('crushed pita chips', 1),
 ('head romaine lettuce, roughly torn', 1),
 ('peaches - peeled, pitted, and diced, or more to taste', 1),
 ('poppy seed dressing (such as Briannas®)', 1),
 ('diced cooked chicken (optional)', 1),
 ('(6 ounce) fillets swai fish', 1),
 ('minced banana peppers', 1),
 ('habanero peppers, minced', 1),
 ('date, pitted', 1),
 ('wedge fresh pineapple (optional)', 1),
 ('whole freshly roasted coffee beans', 1),
 ('maple almond butter', 1),
 ('canned chickpeas (garbanzo beans)', 1),
 ('ginger-miso dressing, or to taste', 1),
 ('red onion, cut into small chunks', 1),
 ("frozen artichoke hearts (such as Trader Joe's®), thawed and drained", 1),
 ('green tea bag', 1),
 ('vanilla 

 ('(1 1/2-pound) salmon fillet, cut into 2-inch cubes', 1),
 ('cherry-flavored Kentucky bourbon whiskey (such as Evan Williams®), or more '
  'as desired',
  1),
 ("bourbon whiskey (such as Jack Daniel's®)", 1),
 ('Italian seasoned ground turkey', 1),
 ('(5.7 ounce) package Knorr® Rice Sides™ - Creamy Chicken', 1),
 ('(10 ounce) can low-sodium diced tomatoes and green chilies', 1),
 ('(16 ounce) can low-sodium refried beans', 1),
 ('(3 ounce) package cook-and-serve vanilla pudding (not instant)', 1),
 ('baby bella mushrooms, sliced, or more to taste', 1),
 ('(16 ounce) can Italian-style crushed tomatoes, undrained', 1),
 ('(10 ounce) package chopped frozen spinach', 1),
 ('cooked roast chicken meat', 1),
 ('yam, cut into chunks', 1),
 ('(12 ounce) package medium-firm tofu, cubed and patted dry', 1),
 ('(12 ounce) 1 1/2-inch thick rib eye steak, thawed', 1),
 ('(2 1/2 pound) 2-inch thick porterhouse steak, at room temperature', 1),
 ('hickory wood chips, soaked (optional)', 1),
 ('turke

 ('jalapeno, cut into spirals', 1),
 ('prepared tostada shells', 1),
 ('fresh pomegranate seeds', 1),
 ('Balsamic Drizzle:', 1),
 ('loaf crusty sourdough or ciabatta bread, sliced', 1),
 ('Olive oil, to drizzle over bread slices and avocados', 1),
 ('(8 ounce) package Stella® fresh mozzarella, sliced', 1),
 ('panko breadcrumbs', 1),
 ('grated Stella® Parmesan cheese', 1),
 ('(8 ounce) package refrigerated butter-flavored crescent rolls', 1),
 ('shredded Stella® mozzarella cheese', 1),
 ('Stella® Parmesan cheese, for topping', 1),
 ('(4 ounce) package Salemville® blue cheese', 1),
 ('powdered Thai tea mix, or to taste', 1),
 ('Shredded Monterey Jack cheese, thinly sliced lettuce, sliced ripe olives, '
  'chopped tomatoes',
  1),
 ('wild raspberries', 1),
 ('fresh cherries, stems removed', 1),
 ('fresh blackberries, washed and drained well', 1),
 ('(10 ounce) can diced tomatoes and green chiles (such as RO*TEL®), drained '
  '(optional)',
  1),
 ('vanilla and honey Greek yogurt (such as 

 ('stevia sweetener (such as Truvia®), or more to taste', 1),
 ('Curd Filling:', 1),
 ('(2.5 ounce) instant vanilla pudding mix', 1),
 ('coarsely crushed gingersnap cookies', 1),
 ('(8 ounce) package refrigerated crescent roll dough (such as Pillsbury®)', 1),
 ('jelly, or to taste', 1),
 ('roasted whole coffee beans', 1),
 ('shortening, or more if desired (optional)', 1),
 ('chopped coffee beans', 1),
 ("cocoa powder (such as Fry's®), or more as needed", 1),
 ('(10 ounce) container prepared pizza dough', 1),
 ('coarsely chopped, lightly toasted California Walnuts, divided', 1),
 ('thinly sliced ham, torn into 1-inch pieces', 1),
 ('Snipped fresh rosemary', 1),
 ('firm but ripe pear, cored and cut into thin bite-size pieces', 1),
 ('frozen cooked scallops', 1),
 ('(12 ounce) package frozen mixed vegetables (carrots, green beans, red bell '
  'peppers)',
  1),
 ('green apple, cut into cubes', 1),
 ('(14 ounce) package licorice string', 1),
 ('(10.5 ounce) package rainbow candy belts (suc

 ('pluots, pitted', 1),
 ('bone-in pork butt', 1),
 ('Wood Chips:', 1),
 ("whiskey barrel wood chips (such as Jack Daniel's®)", 1),
 ('apple wood chips', 1),
 ('bunch sage, chopped', 1),
 ('shredded smoked pork', 1),
 ('smoked turkey leg meat, cooked and chopped', 1),
 ('pork back ribs, membrane removed', 1),
 ('pple wood chips, soaked', 1),
 ('capers, drained and smashed', 1),
 ('beaten egg whites', 1),
 ('cubes chicken bouillon granules', 1),
 ('Anaheim chile peppers, stemmed', 1),
 ('clove garlic, peeled and crushed', 1),
 ('Idaho potatoes, each cut into 8 wedges', 1),
 ("(12 ounce) bottle garlic and cilantro marinade (such as Stubb's®)", 1),
 ('flatbreads', 1),
 ('mild salsa (such as Goya®)', 1),
 ('ube (purple yam), peeled and cut into 1/4-inch-thick fries', 1),
 ('sriracha-flavored salt', 1),
 ('purple sweet potato, or more to taste', 1),
 ('cacao powder, or more to taste', 1),
 ('rice whipped topping, or to taste', 1),
 ('vegan chocolate shavings, or to taste', 1),
 ('(4 ounce) 